In [128]:
import os
import re
import sys
import csv
import time
import tqdm
import nltk
import math
import string
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn import metrics
from sklearn import tree
from sklearn import datasets
from sklearn.svm import LinearSVC
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import Normalizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.naive_bayes import BernoulliNB
from sklearn.decomposition import TruncatedSVD
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import KFold
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords
from nltk.stem import *
from nltk.corpus import wordnet
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import normalize
from sklearn.feature_selection import chi2
from scipy.stats import uniform
from scipy.stats import randint
#from spellchecker import SpellChecker #need to install for some computers
import random
#from Test import * 
from sklearn.utils import shuffle
from sklearn.preprocessing import MaxAbsScaler



stops = ["a", "about", "above", "across", "after", "afterwards",\
         "again", "all", "almost", "alone", "along", "already", "also",\
         "although", "always", "am", "among", "amongst", "amoungst", "amount", "an", "and",\
         "another", "any", "anyhow", "anyone", "anything", "anyway", "anywhere", "are", "as",\
         "at", "be", "became", "because", "become","becomes", "becoming", "been", "before", \
         "behind", "being", "beside", "besides", "between", "beyond", "both", "but", "by","can",\
         'cannot', "cant", "could", "couldnt", "de", "describe", "do", "done", "each", "eg",'either', "else", "enough", "etc", "even", "ever", "every", "everyone", "everything","everywhere", "except", "few", "find","for","found", "four", "from", "further", "get","give", "go", "had", "has", "hasnt", "have", "he", "hence", "her", "here", "hereafter","hereby", "herein", "hereupon", "hers", "herself", "him", "himself", "his", "how","however", "i", "ie", "if", "in", "indeed", "is", "it", "its", "itself", "keep", "least","less", "ltd", "made", "many", "may", "me", "meanwhile", "might", "mine", "more", "moreover","most", "mostly", "much", "must", "my", "myself", "name", "namely", "neither", "never", \
         "nevertheless", "next","no", "nobody", "none", "noone", "nor", "not", "nothing", "now","nowhere", "of", "off", "often", "on", "once", "one", "only", "onto", "or", "other", \
         "others", "otherwise", "our", "ours", "ourselves", "out", "over", "own", "part","perhaps","please", "put", "rather", "re", "same", "see", "seem", "seemed", "seeming", "seems", "she","should","since", "sincere","so", "some", "somehow", "someone", "something", "sometime","sometimes", "somewhere", "still", "such", "take","than", "that", "the", "their", "them", \
         "themselves", "then", "thence", "there", "thereafter", "thereby", "therefore", "therein","thereupon", "these", "they","this", "those", "though", "through", "throughout","thru", "thus", "to", "together", "too", "toward", "towards","under", "until", "up", "upon", "us",\
         "very", "was", "we", "well", "were", "what", "whatever", "when",\
         "whence", "whenever", "where", "whereafter", "whereas", "whereby",\
         "wherein", "whereupon", "wherever", "whether", "which", "while", \
         "who", "whoever", "whom", "whose", "why", "will", "with",\
         "within", "without", "would", "yet", "you", "your", "yours", "yourself", "yourselves"]



feature_names = []

vectorizer = TfidfVectorizer(ngram_range=(1,1),stop_words='english',norm='l2',max_df = 0.995,min_df=2,sublinear_tf=False)
#vectorizer = CountVectorizer(ngram_range=(1,2),stop_words='english',binary=False)

corpus_train = pd.read_csv("reddit_train.csv",usecols=['comments','subreddits'],delimiter=',',sep='\s*,\s*')
corpus_test = pd.read_csv("reddit_train.csv",usecols=['comments','subreddits'],delimiter=',',sep='\s*,\s*')
#corpus_test = pd.read_csv("reddit_test.csv",usecols=['comments','id'],delimiter=',',sep='\s*,\s*')
#random.shuffle(corpus_train)
#corpus_test = corpus_train["comments"]

#corpus_test = corpus_train[60000:]
corpus_train = shuffle(corpus_train)
corpus_test = corpus_train[:10000]
corpus_train = corpus_train[10000:]



english_words = set(nltk.corpus.words.words()\
                    + nltk.corpus.gutenberg.words()\
                    + nltk.corpus.webtext.words()\
                    + nltk.corpus.nps_chat.words()\
                    + nltk.corpus.brown.words() + nltk.corpus.reuters.words())

#spell = SpellChecker()

# def is_english_word(x):
#     return (spell.correction(x) in english_words)
           
def misspell(x):
    if "aaa" not in x and "bbb" not in x and "ccc" not in x and "ddd" not in x \
    and "eee" not in x and "fff" not in x and "ggg" not in x and "hhh" not in x \
    and "iii" not in x and "jjj" not in x and "kkk" not in x and "lll" not in x and "mmm" not in x and "nnn" not in x \
    and "ooo" not in x and "ppp" not in x and "qqq" not in x and "rrr" not in x and "sss" not in x and "ttt" not in x \
    and "uuu" not in x and "vvv" not in x and "www" not in x and "xxx" not in x and "yyy" not in x and "zzz" not in x: #\
    #and "aa" not in x and "zz" not in x:
        return True
    else:
        return False
    

# delete_list = ["aaa" not in x,"bbb" not in x,"ccc" not in x,"ddd" not in x,"eee" not in x,"fff" not in x,"ggg" not in x,\
#                "hhh" not in x,"iii" not in x,"jjj" not in x,"kkk" not in x,"lll" not in x,"mmm" not in x,"nnn" not in x,\
#                "ooo" not in x,"ppp" not in x,"qqq" not in x,"rrr" not in x,"sss" not in x,"ttt" not in x
#                ,"uuu" not in x,"vvv" not in x,"www" not in x,"xxx" not in x,"yyy" not in x,"zzz" not in x]

# a helper function to process one comment
def preprocess_text(text): 
    text = text.lower().split()
    stops = set(stopwords.words("english"))
    text = [w for w in text if not w in stops and len(w) >= 3]
    text = " ".join(text)
    text = re.sub(r"what's", "what is ", text)
    text = re.sub(r"\'s", " ", text)
    text = re.sub(r"\'ve", " have ", text)
    text = re.sub(r"n't", " not ", text)
    text = re.sub(r"i'm", "i am ", text)
    text = re.sub(r"\'re", " are ", text)
    text = re.sub(r"\'d", " would ", text)
    text = re.sub(r"\'ll", " will ", text)
    text = re.sub(r",", " ", text)
    text = re.sub(r"\.", " ", text)
    text = re.sub(r"!", " ! ", text)
    text = re.sub(r"\/", " ", text)
    text = re.sub(r"\^", " ^ ", text)
    text = re.sub(r"\+", " + ", text)
    text = re.sub(r"\-", " - ", text)
    text = re.sub(r"\=", " = ", text)
    text = re.sub(r"'", " ", text)
    text = re.sub(r"^https?:\/\/.*[\r\n]*","", text)
    text = re.sub(r'[^a-zA-Z0-9\s]', ' ',text)
    text = text.split()
    
    # lemmatization
    lemma = nltk.wordnet.WordNetLemmatizer()
    text = [lemma.lemmatize(word) for word in text]
    
#     # stemming
#     text = [PorterStemmer().stem(word) for word in text]
    
    text_final = []
    
    # clean all non-English words, numbers, and other weirdos, stopwords
    for x in text:
        #x = spell.correction(x)
        if x.isalpha() and len(x)<20 and len(x) > 1 and misspell(x) and x not in stops: #and is_english_word(x):
#             if len(x) >10:
#                 text_final.append(PorterStemmer().stem(x))
#             else:
            text_final.append(x)
    
    text = " ".join(text_final)
    return text


to_delete = []

# the major function to process the training dataset
# returns (1) a matrix of all training features x (2) a numpy array of y labels
def preprocess():
    df = corpus_train.copy()
    df['comments'] = df['comments'].map(lambda x: preprocess_text(x))
    y_train = df["subreddits"].to_numpy()
    global vectorizer
    x_train = vectorizer.fit_transform(df['comments'])
    
    print(vectorizer.get_feature_names())
    global feature_names
    feature_names = vectorizer.get_feature_names()
    featname=vectorizer.get_feature_names()
    chi_squared,pval = chi2(x_train, y_train)
    featname = pd.DataFrame(featname)
    chi_2 = pd.DataFrame(chi_squared)
    pval = pd.DataFrame(pval)

    data = pd.concat([featname,chi_2,pval],axis=1)
    data.columns = ["word","chi_squared","pval"]
    data = data.sort_values("pval",axis=0)
    
    global to_delete
    to_delete = list(data.index[15000:])     # unigram 保留10000-15000之间最高
    all_cols = np.arange(x_train.shape[1])
    cols_to_keep = np.where(np.logical_not(np.in1d(all_cols, to_delete)))[0]
    x_train = x_train[:, cols_to_keep]

    scalar = MaxAbsScaler()
    x_train = scalar.fit_transform(x_train)
    return x_train, y_train


# function to process the testing set
# returns the matrix of all testing features
def preprocess_testing():
    df = corpus_test.copy()
    #print(df)
    #df = df['comments']
    df['comments'] = df['comments'].map(lambda x: preprocess_text(x))
    #df = df.map(lambda x: preprocess_text(x))
    #y_train = df["subreddits"].to_numpy()
    global vectorizer
    x_train = vectorizer.transform(df["comments"])
    all_cols = np.arange(x_train.shape[1])
    global to_delete
    cols_to_keep = np.where(np.logical_not(np.in1d(all_cols, to_delete)))[0]
    x_train = x_train[:, cols_to_keep]
    scalar = MaxAbsScaler()
    x_train = scalar.fit_transform(x_train)
    return x_train
    

In [129]:
x,y = preprocess()

['00', '000', '000k', '000th', '003', '004', '005', '00s', '01', '011', '012', '013', '017', '019', '02', '022', '026', '028', '03', '033', '039', '04', '0460', '05', '059', '06', '063', '07', '07112017', '07122017', '072', '08', '085', '087', '088', '08th', '09', '092', '099', '0a', '0ahttp', '0anote', '0aremindme', '0d', '0dmy', '0ing', '0s', '10', '100', '1000', '10000', '100000', '1000x', '100bn', '100g', '100k', '100m', '100mb', '100mg', '100mph', '100s', '100sr', '100th', '100x', '101', '102', '1024', '103', '104', '105', '106', '1060', '107', '1070', '108', '1080', '1080p', '109', '10am', '10ft', '10h', '10ish', '10k', '10m', '10mil', '10min', '10pm', '10s', '10th', '10x', '11', '110', '1100', '110s', '111', '112', '1120', '113', '114', '115', '115m', '116', '117', '118', '1186', '119', '11am', '11pm', '11th', '12', '120', '1200', '120k', '120m', '121', '122', '123', '124', '125', '125k', '126', '127', '128', '1280', '128tick', '12g', '12k', '12m', '12s', '12th', '13', '130', '1

In [130]:
print(len(feature_names))

32693


In [131]:
x2 = preprocess_testing()

In [132]:
from sklearn.metrics import accuracy_score

clf = LinearSVC(C=0.5,loss='hinge',intercept_scaling=0.0016)
clf.fit(x,y)
prediction = clf.predict(x2)
accuracy_score(prediction,corpus_test["subreddits"])

0.5679

In [ ]:
def predictCSV(model,test_y):
    result = model.predict(test_y)
    np.savetxt("prediction.csv", np.dstack((np.arange(0, result.size),result))[0],"%s,%s",header="Id,Category")

In [41]:
clf = MultinomialNB(alpha=1)
#x,y = preprocess()

model_validate(clf,x,y)

Result of held-out validation on  MultinomialNB
                 precision    recall  f1-score   support

      AskReddit       0.29      0.35      0.32       570
GlobalOffensive       0.65      0.62      0.64       576
          Music       0.65      0.65      0.65       650
      Overwatch       0.61      0.71      0.66       586
          anime       0.57      0.65      0.61       543
       baseball       0.75      0.61      0.68       620
         canada       0.47      0.48      0.48       633
     conspiracy       0.39      0.45      0.42       572
         europe       0.53      0.53      0.53       603
          funny       0.27      0.21      0.23       597
  gameofthrones       0.78      0.73      0.75       610
         hockey       0.70      0.63      0.66       600
leagueoflegends       0.74      0.65      0.69       589
         movies       0.55      0.63      0.59       592
            nba       0.68      0.65      0.67       628
            nfl       0.66      0.63   

In [127]:
from sklearn.metrics import accuracy_score

# clf = BernoulliNB(alpha=0.1)
# clf.fit(x,y)
# prediction = clf.predict(x2)
# accuracy_score(prediction,corpus_test["subreddits"])


from sklearn.model_selection import GridSearchCV

parameters = {
    'C':(0.01,0.05,0.1,0.2,0.25,0.28,0.3,0.35,0.4,0.45,0.5,0.55,0.6,0.7,0.8,0.9,1),
    'intercept_scaling':(0.0001,0.00016,0.0005,0.001,0.01,0.1,0.5,1)
}
mnb = GridSearchCV(LinearSVC(), parameters, cv=5, verbose=1, n_jobs=-1)
res_mnb = mnb.fit(x, y)
print(mnb.best_score_)
print(mnb.cv_results_)


# from sklearn.model_selection import GridSearchCV

# parameters = {
#     'alpha': (0,0.00001,0.000005,0.0001,0.0002,0.0057,0.009,0.01)}
# mnb = GridSearchCV(MultinomialNB(), parameters, cv=5, verbose=1, n_jobs=-1)
# res_mnb = mnb.fit(x, y)
# print(mnb.best_score_)
# print(mnb.cv_results_)

Fitting 5 folds for each of 136 candidates, totalling 680 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:   23.5s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:  1.8min
[Parallel(n_jobs=-1)]: Done 434 tasks      | elapsed:  5.6min
[Parallel(n_jobs=-1)]: Done 680 out of 680 | elapsed: 10.2min finished


0.5640166666666667
{'mean_fit_time': array([ 4.33871589,  4.33226805,  4.33554177,  4.30211148,  4.29159627,
        4.46995764,  4.62034545,  4.6417727 ,  4.16303329,  4.12007937,
        4.13238025,  4.25399957,  4.35736561,  5.13182068,  4.95832033,
        5.08202305,  4.32234821,  4.14120855,  3.97098169,  4.32155447,
        4.56687698,  5.04829464,  4.95951071,  5.15146279,  4.7186532 ,
        4.85306902,  4.3505208 ,  4.23544855,  4.19269338,  4.38286018,
        4.54038949,  5.33676839,  4.19097137,  4.16948071,  4.10847239,
        4.15946083,  4.46886697,  5.38805561,  6.76068778,  8.35800757,
        6.22252574,  6.23708482,  6.26528192,  6.26240525,  6.34196377,
        6.75175886,  7.03447962,  8.63358579,  6.4082294 ,  6.37410469,
        6.31339378,  6.37529435,  6.42211723,  6.77725396,  7.07526917,
        8.82772074,  6.63569522,  6.47231269,  6.53629465,  6.56496525,
        6.63816557,  6.97168622,  7.37910261,  9.34990973,  6.86266522,
        6.73826852,  6.8132

       108, 111, 114, 126, 127, 128])}


In [39]:
# is_anime = corpus_train["subreddits"] == "anime"        
# df = corpus_train[is_anime]["comments"]
# print(df.to_string())

36432    Ahhh... The memories. Asa Made Jugyou Chu got ...
68952    I thought the pacing of this first episode was...
51595    ~~but I only recieve my orders from Nuke on Su...
49769    I didn't point it out in my original post but ...
28500    I don't know, maybe? I haven't learnt anything...
57322    Kadokawa uploaded the op and ed to their YT ch...
56101    Definitely want to see this with twitch chat, ...
18915    I dunno, Little Witch Academia has a bunch of ...
68844    Re: zero, thout the first episode was shit, ne...
24128    I have seen most of these, and at least had al...
10621    Nano Shinonome\n\n/r/transpassing \n\nEdward E...
5930     Ah OK then, yeah I'll hold off a bit, don't kn...
64892    &gt; I love her but she is really... messed up...
37692    Hahahahaha but you don't understand [food item...
41836    that's fine. Soon the first thing you'll think...
1505     god this is so chilling.\nthis anime will also...
13889    Can you really make that much money with that?.

30825    Why does there need to be a label for it? Too ...


In [77]:
from tqdm import tqdm
counter = 0
for i in tqdm(range(x2.shape[1])):
    if sum(x2[:,i].toarray()) == 0:
        counter += 1
print(counter)


  3%|██                                                                            | 405/15000 [00:15<09:09, 26.54it/s]


  5%|████▏                                                                         | 813/15000 [00:30<08:56, 26.42it/s]


  8%|██████▎                                                                      | 1221/15000 [00:45<08:40, 26.47it/s]


 11%|████████▎                                                                    | 1629/15000 [01:01<08:35, 25.95it/s]


 14%|██████████▍                                                                  | 2037/15000 [01:17<08:14, 26.21it/s]


...

 92%|██████████████████████████████████████████████████████████████████████▏     | 13854/15000 [09:05<00:43, 26.33it/s]


 95%|████████████████████████████████████████████████████████████████████████▎   | 14262/15000 [09:20<00:27, 26.95it/s]


 98%|██████████████████████████████████████████████████████████████████████████▎ | 14670/15000 [09:36<00:12, 26.05it/s]


100%|████████████████████████████████████████████████████████████████████████████| 15000/15000 [09:48<00:00, 27.04it/s]

0


In [45]:
from sklearn.svm import SVC
clf = SVC()
#x,y = preprocess()

model_validate(clf,x,y)


D:\PROGRAMS\Anaconda\lib\site-packages\sklearn\svm\base.py:193: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)


KeyboardInterrupt: 

In [69]:
from sklearn.model_selection import GridSearchCV

parameters = {
    'alpha': (0,0.00001,0.000005,0.0001,0.0002,0.0057,0.009,0.01)}
mnb = GridSearchCV(MultinomialNB(), parameters, cv=5, verbose=1, n_jobs=-1)
res_mnb = mnb.fit(x, y)
print(mnb.best_score_)
print(mnb.cv_results_)

Fitting 5 folds for each of 8 candidates, totalling 40 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  40 out of  40 | elapsed:    3.5s finished


0.6137142857142858
{'mean_fit_time': array([0.45087161, 0.4298182 , 0.42348542, 0.37805114, 0.37943988,
       0.35969896, 0.33658566, 0.33509798]), 'std_fit_time': array([0.01727471, 0.03495638, 0.0178405 , 0.04145974, 0.03598418,
       0.02649358, 0.03323519, 0.02226683]), 'mean_score_time': array([0.04523506, 0.04642501, 0.04235783, 0.04285479, 0.03501735,
       0.03432312, 0.0306529 , 0.02559304]), 'std_score_time': array([0.00299958, 0.00138869, 0.0062786 , 0.00461674, 0.00286787,
       0.00403407, 0.00189243, 0.00357163]), 'param_alpha': masked_array(data=[0, 1e-05, 5e-06, 0.0001, 0.0002, 0.0057, 0.009, 0.01],
             mask=[False, False, False, False, False, False, False, False],
       fill_value='?',
            dtype=object), 'params': [{'alpha': 0}, {'alpha': 1e-05}, {'alpha': 5e-06}, {'alpha': 0.0001}, {'alpha': 0.0002}, {'alpha': 0.0057}, {'alpha': 0.009}, {'alpha': 0.01}], 'split0_test_score': array([0.60892857, 0.6125    , 0.61242857, 0.61414286, 0.61407143,
     

In [43]:
print(x.shape)

(60000, 70000)


In [44]:
x2 = preprocess_testing()

In [45]:
print(x2.shape)

(10000, 1760323)


In [46]:
all_cols = np.arange(x2.shape[1])
cols_to_keep = np.where(np.logical_not(np.in1d(all_cols, to_delete)))[0]
x2 = x2[:, cols_to_keep]
print(x2.shape)



(10000, 70000)


In [61]:
clf = MultinomialNB(alpha=0.2)
clf.fit(x,y)

MultinomialNB(alpha=0.2, class_prior=None, fit_prior=True)

In [62]:
corpus_test2 = pd.read_csv("reddit_train.csv",usecols=['subreddits'],delimiter=',')

corpus_test2 = corpus_test2[60000:]
print(x.shape)
print(x2.shape)

from sklearn.metrics import accuracy_score
prediction = clf.predict(x2[:,:70000])
accuracy_score(prediction,corpus_test2)

(60000, 70000)
(10000, 70000)


0.5685

In [8]:
print(x2)

  (0, 266151)	0.1689965052000956
  (0, 403790)	0.1689965052000956
  (0, 647801)	0.1689965052000956
  (0, 651929)	0.1689965052000956
  (0, 165572)	0.1689965052000956
  (0, 557705)	0.1689965052000956
  (0, 8572)	0.1689965052000956
  (0, 824436)	0.1689965052000956
  (0, 759002)	0.1689965052000956
  (0, 429584)	0.1689965052000956
  (0, 431643)	0.1689965052000956
  (0, 88366)	0.1689965052000956
  (0, 824440)	0.1689965052000956
  (0, 675056)	0.14905342135604702
  (0, 266150)	0.1689965052000956
  (0, 403789)	0.1689965052000956
  (0, 647800)	0.1689965052000956
  (0, 651928)	0.1689965052000956
  (0, 165571)	0.1689965052000956
  (0, 557704)	0.1689965052000956
  (0, 8571)	0.1689965052000956
  (0, 824435)	0.1689965052000956
  (0, 759001)	0.1689965052000956
  (0, 429582)	0.16254179281619643
  (0, 431639)	0.1544098169351651
  :	:
  (29999, 560335)	0.19925473729095602
  (29999, 799141)	0.19925473729095602
  (29999, 629681)	0.19925473729095602
  (29999, 80958)	0.19925473729095602
  (29999, 411560)	0.1

In [3]:
feature_names

['ab',
 'ab ab',
 'ab ab tough',
 'ab abpc',
 'ab abpc doc',
 'ab actually',
 'ab appreciate',
 'ab appreciate player',
 'ab april',
 'ab april people',
 'ab batter',
 'ab batter try',
 'ab bd',
 'ab bd bb',
 'ab bloop',
 'ab bloop single',
 'ab bverfgg',
 'ab bverfgg http',
 'ab called',
 'ab called count',
 'ab came',
 'ab came min',
 'ab chance',
 'ab chance age',
 'ab coliseum',
 'ab coliseum wa',
 'ab contract',
 'ab contract contingent',
 'ab day',
 'ab deal',
 'ab deal luxury',
 'ab demotion',
 'ab demotion think',
 'ab econ',
 'ab econ macro',
 'ab gave',
 'ab gave humbled',
 'ab got',
 'ab got average',
 'ab green',
 'ab green odell',
 'ab ha',
 'ab ha played',
 'ab higha',
 'ab higha damn',
 'ab hit',
 'ab hit home',
 'ab http',
 'ab http streamable',
 'ab jc',
 'ab jc fit',
 'ab jc plus',
 'ab kitchen',
 'ab kitchen mean',
 'ab leaving',
 'ab leaving guy',
 'ab leaving wa',
 'ab like',
 'ab like receiving',
 'ab ndp',
 'ab ndp managed',
 'ab obj',
 'ab obj aj',
 'ab pay',
 '

In [54]:
clf = LinearSVC(C=2.08)
#x,y = preprocess()

model_validate(clf,x,y)



Result of held-out validation on  LinearSVC
                 precision    recall  f1-score   support

      AskReddit       0.28      0.30      0.29       684
GlobalOffensive       0.64      0.70      0.67       680
          Music       0.69      0.71      0.70       693
      Overwatch       0.73      0.71      0.72       657
          anime       0.68      0.66      0.67       706
       baseball       0.72      0.64      0.68       750
         canada       0.49      0.48      0.49       725
     conspiracy       0.42      0.48      0.45       692
         europe       0.53      0.56      0.55       689
          funny       0.29      0.27      0.28       703
  gameofthrones       0.80      0.77      0.78       694
         hockey       0.66      0.62      0.64       711
leagueoflegends       0.72      0.69      0.70       694
         movies       0.61      0.64      0.62       707
            nba       0.71      0.68      0.69       716
            nfl       0.64      0.65      0

In [64]:
print(feature_names)

['aba', 'aback', 'abadi', 'abam', 'abandon', 'abandoned', 'abandoning', 'abandonment', 'abandonned', 'abandonware', 'abaya', 'abb', 'abbas', 'abbey', 'abbotsford', 'abbreviated', 'abbreviation', 'abby', 'abc', 'abck', 'abd', 'abdelhak', 'abdelkader', 'abdicate', 'abdomen', 'abdominal', 'abducted', 'abducting', 'abduction', 'abductive', 'abdul', 'abdullah', 'abe', 'abeast', 'abed', 'abel', 'abell', 'abendblatt', 'aberation', 'aberdeen', 'aberg', 'aberration', 'abetting', 'abeyta', 'abgelehnt', 'abgrenzung', 'abhor', 'abhorrent', 'abhors', 'abidal', 'abide', 'abiding', 'abilify', 'abilites', 'abilitie', 'ability', 'abillities', 'abilties', 'abin', 'abingdon', 'abington', 'abit', 'abitur', 'abject', 'ablaze', 'able', 'abled', 'ableton', 'abliged', 'abn', 'abnormal', 'abnormality', 'abnormally', 'aboard', 'abode', 'abogado', 'aboiut', 'abolish', 'abolished', 'abolition', 'abolitionist', 'abolve', 'abominably', 'abomination', 'aboot', 'aboriginal', 'aborigine', 'aborigionals', 'abort', 'abo

In [69]:
featname=feature_names
chi_squared,pval = chi2(x, y)
featname = pd.DataFrame(featname)
chi_2 = pd.DataFrame(chi_squared)
pval = pd.DataFrame(pval)

data = pd.concat([featname,chi_2,pval],axis=1)
data.columns = ["word","chi_squared","pval"]
data = data.sort_values("pval",axis=0)

to_delete_probable = list(data.index[10000:])     # 保留10000-15000之间最高
to_delete=[]


from tqdm import tqdm
#suspicious_word_index = []
spell = SpellChecker()
for i in tqdm(to_delete_probable):
    if spell.correction(feature_names[i]) not in english_words:
        to_delete.append(i)








  0%|                                                                                        | 0/47430 [00:00<?, ?it/s]


  0%|                                                                              | 3/47430 [00:01<8:38:57,  1.52it/s]


  0%|                                                                             | 12/47430 [00:04<7:05:10,  1.86it/s]


  0%|                                                                             | 19/47430 [00:05<5:41:05,  2.32it/s]


  0%|                                                                            | 20/47430 [00:09<19:13:16,  1.46s/it]


  0%|                                                                            | 23/47430 [00:10<15:10:37,  1.15s/it]


  0%|                                                                            | 24/47430 [00:12<17:08:05,  1.30s/it]


  0%|                                                                            | 26/47430 [00:13<14:00:15,  1.06s/it]


  0%|                

  1%|█▏                                                                          | 704/47430 [04:23<4:33:42,  2.85it/s]


  1%|█▏                                                                          | 706/47430 [04:27<9:39:36,  1.34it/s]


  1%|█▏                                                                          | 708/47430 [04:28<9:15:28,  1.40it/s]


  2%|█▏                                                                          | 721/47430 [04:29<6:47:34,  1.91it/s]


  2%|█▏                                                                          | 727/47430 [04:31<6:04:08,  2.14it/s]


  2%|█▏                                                                          | 736/47430 [04:32<4:51:43,  2.67it/s]


  2%|█▏                                                                          | 737/47430 [04:33<6:39:25,  1.95it/s]


  2%|█▏                                                                          | 748/47430 [04:37<5:59:41,  2.16it/s]


  2%|█▏                 

  3%|██                                                                        | 1315/47430 [08:32<13:20:10,  1.04s/it]


  3%|██                                                                        | 1318/47430 [08:35<12:49:13,  1.00s/it]


  3%|██                                                                        | 1319/47430 [08:38<20:04:47,  1.57s/it]


  3%|██                                                                        | 1329/47430 [08:41<15:19:46,  1.20s/it]


  3%|██                                                                        | 1330/47430 [08:45<22:49:14,  1.78s/it]


  3%|██                                                                        | 1342/47430 [08:46<16:32:41,  1.29s/it]


  3%|██                                                                        | 1346/47430 [08:48<12:57:23,  1.01s/it]


  3%|██                                                                        | 1349/47430 [08:50<11:50:52,  1.08it/s]


  3%|██                 

  4%|███                                                                       | 1977/47430 [12:42<11:38:50,  1.08it/s]


  4%|███▏                                                                       | 1996/47430 [12:43<8:22:12,  1.51it/s]


  4%|███▏                                                                       | 2000/47430 [12:44<6:38:17,  1.90it/s]


  4%|███                                                                       | 2001/47430 [12:46<11:16:53,  1.12it/s]


  4%|███▏                                                                       | 2010/47430 [12:50<9:32:17,  1.32it/s]


  4%|███▏                                                                      | 2011/47430 [12:51<12:07:01,  1.04it/s]


  4%|███▏                                                                      | 2015/47430 [12:54<10:56:30,  1.15it/s]


  4%|███▏                                                                      | 2018/47430 [13:02<17:28:42,  1.39s/it]


  4%|███▏               

  6%|████▏                                                                      | 2620/47430 [16:53<7:39:16,  1.63it/s]


  6%|████▏                                                                      | 2634/47430 [16:54<5:39:27,  2.20it/s]


  6%|████▏                                                                      | 2643/47430 [16:55<4:25:40,  2.81it/s]


  6%|████▏                                                                      | 2646/47430 [16:58<6:25:34,  1.94it/s]


  6%|████▏                                                                      | 2659/47430 [17:00<5:07:45,  2.42it/s]


  6%|████▏                                                                     | 2661/47430 [17:08<17:11:51,  1.38s/it]


  6%|████▏                                                                     | 2666/47430 [17:10<14:06:08,  1.13s/it]


  6%|████▏                                                                     | 2675/47430 [17:12<10:28:32,  1.19it/s]


  6%|████▏              

KeyboardInterrupt: 

In [ ]:

all_cols = np.arange(x_train.shape[1])
cols_to_keep = np.where(np.logical_not(np.in1d(all_cols, to_delete)))[0]
x_train = x[:, cols_to_keep]

In [4]:
from tqdm import tqdm

index_to_delete = []
index_to_combine = []


for i in tqdm(range(len(feature_names)-1)):
    same_root = [i]
    for j in range(i+1,len(feature_names)):
        if(feature_names[i][0]!=feature_names[j][0]):
            break
        else:
            if PorterStemmer().stem(feature_names[i]) == PorterStemmer().stem(feature_names[j]):
                same_root.append(j)

    index_to_combine.append(same_root)




# from spellchecker import SpellChecker
# spell = SpellChecker()

# wrong_word_index_list = []
# for i in tqdm(range(len(feature_names))):
#     if len(feature_names[i])<=10:
#         if (spell.correction(feature_names[i]) not in english_words):
#             wrong_word_index_list.append(i)

# print(wrong_word_index_list)





100%|██████████████████████████████████████████████████████████████████████████| 57429/57429 [1:07:15<00:00, 14.23it/s]


In [5]:
#print(index_to_combine)
#index_to_combine_plus = [line for line in index_to_combine if len(line)>2]
filtered_lines = list(filter(lambda x: len(x) > 1, index_to_combine))
to_delete_index = []
for i in range(len(filtered_lines)-1):
    for j in range(i+1,min(len(filtered_lines),i+10)):
        if set(filtered_lines[j]) <= set(filtered_lines[i]):
            to_delete_index.append(j)
    

In [6]:
filtered_lines

[[4, 5, 6, 7, 8],
 [5, 6, 7, 8],
 [6, 7, 8],
 [7, 8],
 [15, 16],
 [26, 27, 28, 29],
 [27, 28, 29],
 [28, 29],
 [32, 34],
 [35, 36],
 [46, 48],
 [49, 50, 51],
 [50, 51],
 [55, 56],
 [65, 66],
 [70, 71, 72],
 [71, 72],
 [77, 78],
 [82, 83],
 [85, 86],
 [88, 89, 90, 91],
 [89, 90, 91],
 [90, 91],
 [100, 101],
 [108, 109],
 [120, 121, 122, 123],
 [121, 122, 123],
 [122, 123],
 [128, 129, 130, 131],
 [129, 130, 131],
 [130, 131],
 [132, 133],
 [135, 136],
 [139, 140],
 [145, 147],
 [153, 155],
 [156, 157],
 [159, 160, 161, 162, 163, 164],
 [160, 161, 162, 163, 164],
 [161, 162, 163, 164],
 [162, 163, 164],
 [163, 164],
 [165, 166],
 [169, 170],
 [172, 174, 177],
 [174, 177],
 [175, 176],
 [183, 205],
 [187, 188, 189, 190, 191],
 [188, 189, 190, 191],
 [189, 190, 191],
 [190, 191],
 [192, 193, 194],
 [193, 194],
 [195, 196],
 [197, 198, 199, 200, 201, 203, 204],
 [198, 199, 200, 201, 203, 204],
 [199, 200, 201, 203, 204],
 [200, 201, 203, 204],
 [201, 203, 204],
 [203, 204],
 [206, 207],
 [2

In [7]:

len(filtered_lines) - len(set(to_delete_index))

6994

In [8]:
new_line = []
main_cols = []
for i in range(len(filtered_lines)):
    if i not in set(to_delete_index):
        new_line.append(filtered_lines[i])
        main_cols.append(filtered_lines[i][0])

In [9]:
new_line

[[4, 5, 6, 7, 8],
 [15, 16],
 [26, 27, 28, 29],
 [32, 34],
 [35, 36],
 [46, 48],
 [49, 50, 51],
 [55, 56],
 [65, 66],
 [70, 71, 72],
 [77, 78],
 [82, 83],
 [85, 86],
 [88, 89, 90, 91],
 [100, 101],
 [108, 109],
 [120, 121, 122, 123],
 [128, 129, 130, 131],
 [132, 133],
 [135, 136],
 [139, 140],
 [145, 147],
 [153, 155],
 [156, 157],
 [159, 160, 161, 162, 163, 164],
 [165, 166],
 [169, 170],
 [172, 174, 177],
 [175, 176],
 [183, 205],
 [187, 188, 189, 190, 191],
 [192, 193, 194],
 [195, 196],
 [197, 198, 199, 200, 201, 203, 204],
 [206, 207],
 [209, 210, 211, 212, 213, 214],
 [216, 219],
 [217, 218],
 [221, 222],
 [225, 226, 227, 228],
 [229, 230],
 [231, 232, 233, 234, 235],
 [238, 239, 240, 241, 242],
 [243, 244, 245, 247],
 [251, 252, 253, 254, 255, 256],
 [260, 261, 262],
 [263, 264],
 [267, 268, 269, 270, 271],
 [273, 274],
 [277, 280, 281, 282, 283, 284],
 [294, 297, 309],
 [301, 302, 303, 304, 305, 306, 307],
 [310, 317],
 [318, 319, 321],
 [323, 324, 325, 326, 327],
 [330, 332],

In [10]:
new_line #######
x,y = preprocess()

['aba', 'aback', 'abadi', 'abam', 'abandon', 'abandoned', 'abandoning', 'abandonment', 'abandonned', 'abandonware', 'abaya', 'abb', 'abbas', 'abbey', 'abbotsford', 'abbreviated', 'abbreviation', 'abby', 'abc', 'abck', 'abd', 'abdelhak', 'abdelkader', 'abdicate', 'abdomen', 'abdominal', 'abducted', 'abducting', 'abduction', 'abductive', 'abdul', 'abdullah', 'abe', 'abeast', 'abed', 'abel', 'abell', 'abendblatt', 'aberation', 'aberdeen', 'aberg', 'aberration', 'abetting', 'abeyta', 'abgelehnt', 'abgrenzung', 'abhor', 'abhorrent', 'abhors', 'abidal', 'abide', 'abiding', 'abilify', 'abilites', 'abilitie', 'ability', 'abillities', 'abilties', 'abin', 'abingdon', 'abington', 'abit', 'abitur', 'abject', 'ablaze', 'able', 'abled', 'ableton', 'abliged', 'abn', 'abnormal', 'abnormality', 'abnormally', 'aboard', 'abode', 'abogado', 'aboiut', 'abolish', 'abolished', 'abolition', 'abolitionist', 'abolve', 'abominably', 'abomination', 'aboot', 'aboriginal', 'aborigine', 'aborigionals', 'abort', 'abo

In [23]:
temp = x

In [24]:
from scipy.sparse import csr_matrix
#len(temp[:,2666].toarray())
#temp[:,4] = csr_matrix(temp[:,4].toarray()+temp[:,4].toarray())


In [26]:
from tqdm import tqdm
for i in tqdm(range(len(new_line)-1)):
    temp[:,new_line[i][0]] = csr_matrix(temp[:,new_line[i][0]].toarray() * len(new_line[i]))



  0%|                                                                                         | 0/6993 [00:00<?, ?it/s]

  0%|▏                                                                              | 14/6993 [00:00<00:51, 135.70it/s]

  0%|▎                                                                              | 28/6993 [00:00<00:51, 135.12it/s]

  1%|▍                                                                              | 42/6993 [00:00<00:51, 135.68it/s]

  1%|▌                                                                              | 55/6993 [00:00<00:52, 132.83it/s]

  1%|▊                                                                              | 69/6993 [00:00<00:52, 132.73it/s]

  1%|▉                                                                              | 82/6993 [00:00<00:52, 131.23it/s]

  1%|█                                                                              | 96/6993 [00:00<00:52, 131.61it/s]

  2%|█▏                       

 22%|█████████████████▏                                                            | 1539/6993 [00:14<00:58, 93.80it/s]

 22%|█████████████████▎                                                            | 1549/6993 [00:14<00:58, 93.66it/s]

 22%|█████████████████▍                                                            | 1559/6993 [00:14<00:58, 93.44it/s]

 22%|█████████████████▌                                                            | 1569/6993 [00:14<01:00, 90.39it/s]

 23%|█████████████████▌                                                            | 1579/6993 [00:14<00:58, 92.39it/s]

 23%|█████████████████▋                                                            | 1589/6993 [00:15<00:58, 92.93it/s]

 23%|█████████████████▊                                                            | 1599/6993 [00:15<01:01, 88.05it/s]

 23%|█████████████████▉                                                            | 1608/6993 [00:15<01:01, 87.80it/s]

 23%|██████████████████         

 39%|██████████████████████████████▎                                               | 2719/6993 [00:29<00:58, 73.01it/s]

 39%|██████████████████████████████▍                                               | 2727/6993 [00:29<00:58, 73.20it/s]

 39%|██████████████████████████████▌                                               | 2735/6993 [00:29<00:57, 74.04it/s]

 39%|██████████████████████████████▌                                               | 2743/6993 [00:29<00:57, 73.82it/s]

 39%|██████████████████████████████▋                                               | 2751/6993 [00:29<00:58, 72.67it/s]

 39%|██████████████████████████████▊                                               | 2759/6993 [00:29<00:57, 73.06it/s]

 40%|██████████████████████████████▊                                               | 2767/6993 [00:29<00:59, 71.58it/s]

 40%|██████████████████████████████▉                                               | 2775/6993 [00:29<00:59, 70.67it/s]

 40%|███████████████████████████

 53%|█████████████████████████████████████████▎                                    | 3699/6993 [00:43<00:49, 66.06it/s]

 53%|█████████████████████████████████████████▎                                    | 3706/6993 [00:43<00:49, 66.77it/s]

 53%|█████████████████████████████████████████▍                                    | 3713/6993 [00:43<00:48, 67.19it/s]

 53%|█████████████████████████████████████████▍                                    | 3720/6993 [00:43<00:48, 67.00it/s]

 53%|█████████████████████████████████████████▌                                    | 3727/6993 [00:43<00:48, 67.74it/s]

 53%|█████████████████████████████████████████▋                                    | 3734/6993 [00:44<00:48, 67.77it/s]

 53%|█████████████████████████████████████████▋                                    | 3741/6993 [00:44<00:48, 67.60it/s]

 54%|█████████████████████████████████████████▊                                    | 3748/6993 [00:44<00:48, 67.10it/s]

 54%|███████████████████████████

 68%|████████████████████████████████████████████████████▊                         | 4737/6993 [00:58<00:28, 78.17it/s]

 68%|████████████████████████████████████████████████████▉                         | 4745/6993 [00:58<00:28, 77.87it/s]

 68%|█████████████████████████████████████████████████████                         | 4753/6993 [00:58<00:29, 77.10it/s]

 68%|█████████████████████████████████████████████████████                         | 4762/6993 [00:58<00:28, 78.13it/s]

 68%|█████████████████████████████████████████████████████▏                        | 4770/6993 [00:58<00:28, 77.73it/s]

 68%|█████████████████████████████████████████████████████▎                        | 4778/6993 [00:58<00:28, 77.67it/s]

 68%|█████████████████████████████████████████████████████▍                        | 4786/6993 [00:58<00:28, 78.31it/s]

 69%|█████████████████████████████████████████████████████▍                        | 4794/6993 [00:58<00:27, 78.65it/s]

 69%|███████████████████████████

 85%|██████████████████████████████████████████████████████████████████            | 5928/6993 [01:12<00:12, 84.47it/s]

 85%|██████████████████████████████████████████████████████████████████▏           | 5938/6993 [01:12<00:12, 86.61it/s]

 85%|██████████████████████████████████████████████████████████████████▎           | 5947/6993 [01:13<00:11, 87.42it/s]

 85%|██████████████████████████████████████████████████████████████████▍           | 5956/6993 [01:13<00:12, 85.51it/s]

 85%|██████████████████████████████████████████████████████████████████▌           | 5965/6993 [01:13<00:12, 85.18it/s]

 85%|██████████████████████████████████████████████████████████████████▋           | 5974/6993 [01:13<00:12, 84.58it/s]

 86%|██████████████████████████████████████████████████████████████████▋           | 5984/6993 [01:13<00:11, 86.14it/s]

 86%|██████████████████████████████████████████████████████████████████▊           | 5993/6993 [01:13<00:11, 84.89it/s]

 86%|███████████████████████████

In [27]:
to_delete_from_matrix=[]
for i in range(len(new_line)):
    for j in range(1,len(new_line[i])):
        to_delete_from_matrix.append(new_line[i][j])
to_delete_from_matrix= list(set(to_delete_from_matrix))

In [28]:
to_delete = to_delete_from_matrix
all_cols = np.arange(temp.shape[1])
cols_to_keep = np.where(np.logical_not(np.in1d(all_cols, to_delete)))[0]
temp = temp[:, cols_to_keep]

In [29]:
temp.shape

(70000, 45018)

In [33]:
print(len(main_cols))

6994


In [34]:
from sklearn.preprocessing import normalize
temp2 = normalize(temp,axis=1)

In [35]:
clf = MultinomialNB(alpha=0.0565)
#x,y = preprocess()

model_validate(clf,temp2,y)

Result of k-fold cross validation on  MultinomialNB
0.4842857142857143


In [31]:
x,y = preprocess()
clf = MultinomialNB(alpha=0.0565)
#x,y = preprocess()

model_validate(clf,x,y)

['aba', 'aback', 'abadi', 'abam', 'abandon', 'abandoned', 'abandoning', 'abandonment', 'abandonned', 'abandonware', 'abaya', 'abb', 'abbas', 'abbey', 'abbotsford', 'abbreviated', 'abbreviation', 'abby', 'abc', 'abck', 'abd', 'abdelhak', 'abdelkader', 'abdicate', 'abdomen', 'abdominal', 'abducted', 'abducting', 'abduction', 'abductive', 'abdul', 'abdullah', 'abe', 'abeast', 'abed', 'abel', 'abell', 'abendblatt', 'aberation', 'aberdeen', 'aberg', 'aberration', 'abetting', 'abeyta', 'abgelehnt', 'abgrenzung', 'abhor', 'abhorrent', 'abhors', 'abidal', 'abide', 'abiding', 'abilify', 'abilites', 'abilitie', 'ability', 'abillities', 'abilties', 'abin', 'abingdon', 'abington', 'abit', 'abitur', 'abject', 'ablaze', 'able', 'abled', 'ableton', 'abliged', 'abn', 'abnormal', 'abnormality', 'abnormally', 'aboard', 'abode', 'abogado', 'aboiut', 'abolish', 'abolished', 'abolition', 'abolitionist', 'abolve', 'abominably', 'abomination', 'aboot', 'aboriginal', 'aborigine', 'aborigionals', 'abort', 'abo


Result of k-fold cross validation on  MultinomialNB
0.5519142857142857


In [142]:
for i in tqdm(range(len(new_line))):
    for j in range(1,len(new_line[i])):
        temp[:,new_line[i][0]] = csr_matrix(temp[:,new_line[i][j]].toarray() + temp[:,new_line[i][0]].toarray())





  0%|                                                                                         | 0/6994 [00:00<?, ?it/s]

ValueError: indices and data should have the same size

In [117]:
temp[:,0].toarray()

array([[0.],
       [0.],
       [0.],
       ...,
       [0.],
       [0.],
       [0.]])

In [98]:
set([1,2]) <= set([1,2,3])

True

In [67]:
#print(index_to_combine)
x,y = preprocess()

print(x)




['aba', 'aback', 'abadi', 'abam', 'abandon', 'abandoned', 'abandoning', 'abandonment', 'abandonned', 'abandonware', 'abaya', 'abb', 'abbas', 'abbey', 'abbotsford', 'abbreviated', 'abbreviation', 'abby', 'abc', 'abck', 'abd', 'abdelhak', 'abdelkader', 'abdicate', 'abdomen', 'abdominal', 'abducted', 'abducting', 'abduction', 'abductive', 'abdul', 'abdullah', 'abe', 'abeast', 'abed', 'abel', 'abell', 'abendblatt', 'aberation', 'aberdeen', 'aberg', 'aberration', 'abetting', 'abeyta', 'abgelehnt', 'abgrenzung', 'abhor', 'abhorrent', 'abhors', 'abidal', 'abide', 'abiding', 'abilify', 'abilites', 'abilitie', 'ability', 'abillities', 'abilties', 'abin', 'abingdon', 'abington', 'abit', 'abitur', 'abject', 'ablaze', 'able', 'abled', 'ableton', 'abliged', 'abn', 'abnormal', 'abnormality', 'abnormally', 'aboard', 'abode', 'abogado', 'aboiut', 'abolish', 'abolished', 'abolition', 'abolitionist', 'abolve', 'abominably', 'abomination', 'aboot', 'aboriginal', 'aborigine', 'aborigionals', 'abort', 'abo


  (0, 29360)	0.20022594191910897
  (0, 14190)	0.15775115563721837
  (0, 7907)	0.11740190288167779
  (0, 42071)	0.1723313388019609
  (0, 9505)	0.15701205849058875
  (0, 50247)	0.13392036335509133
  (0, 12684)	0.19056621306873878
  (0, 49501)	0.23458446228031543
  (0, 56743)	0.08516746372577937
  (0, 4649)	0.09539836510311284
  (0, 51767)	0.22717098530336569
  (0, 35021)	0.15775115563721837
  (0, 14997)	0.1977067724450827
  (0, 50637)	0.07728236382946274
  (0, 51539)	0.16573477387875873
  (0, 19417)	0.08938147609101936
  (0, 55951)	0.11864793162774175
  (0, 20369)	0.1760204656970901
  (0, 47897)	0.14140138741898675
  (0, 30242)	0.2412815872074171
  (0, 26124)	0.18691498233158588
  (0, 46893)	0.16558409629962711
  (0, 37128)	0.07666144854857686
  (0, 41636)	0.12030554299058105
  (0, 1888)	0.13776730808959703
  :	:
  (69998, 28745)	0.17320360534707682
  (69998, 22108)	0.19524994188505868
  (69998, 50407)	0.15127222268163704
  (69998, 38849)	0.18427540349679816
  (69998, 33754)	0.165390761

MemoryError: 

In [36]:
all_cols = np.arange(x.shape[1])
cols_to_keep = np.where(np.logical_not(np.in1d(all_cols, wrong_word_index_list)))[0]
x = x[:, cols_to_keep]

In [37]:
print(x.shape)

(70000, 40956)


In [38]:
clf = MultinomialNB(alpha=0.0565)
#x,y = preprocess()

model_validate(clf,x,y)

Result of k-fold cross validation on  MultinomialNB
0.49660000000000004


In [33]:
x,y = preprocess()
featname=vectorizer.get_feature_names()
#print(len(featname))
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import normalize
from sklearn.feature_selection import chi2

chi2,pval = chi2(x, y)
featname = pd.DataFrame(featname)
chi2 = pd.DataFrame(chi2)
pval = pd.DataFrame(pval)

data=pd.concat([featname,chi2,pval],axis=1)
data.columns = ["word","chi2","pval"]
data=data.sort_values("pval",axis=0)

to_delete = list(data.index[10000:])     # 保留10000-15000之间最高

all_cols = np.arange(x.shape[1])
cols_to_keep = np.where(np.logical_not(np.in1d(all_cols, to_delete)))[0]
m = x[:, cols_to_keep]

clf = MultinomialNB(alpha=0.15,fit_prior=True)

model_validate(clf,m,y)



KeyboardInterrupt: 

In [119]:
type(x)

scipy.sparse.csr.csr_matrix

In [120]:
print(x.shape)

(70000, 58846)


In [121]:
# import scipy
# def delete_rows_csr(mat, indices):
#     """
#     Remove the rows denoted by ``indices`` form the CSR sparse matrix ``mat``.
#     """
#     if not isinstance(mat, scipy.sparse.csr_matrix):
#         raise ValueError("works only for CSR format -- use .tocsr() first")
#     #indices = list(indices)
#     mask = np.ones(mat.shape, dtype=bool)
#     mask[:,indices] = False
#     return mat[mask]

to_delete = list(data.index[10000:])     # 保留10000-15000之间最高

all_cols = np.arange(x.shape[1])
cols_to_keep = np.where(np.logical_not(np.in1d(all_cols, to_delete)))[0]
m = x[:, cols_to_keep]

In [122]:
#print(data['pval'])

#print(sorted(x,reverse=True))
print(m.shape)



#clf = LogisticRegression()
from sklearn.svm import SVC
#clf = SVC(gamma='auto')
clf = MultinomialNB(alpha=0.15,fit_prior=False)

(70000, 10000)


In [123]:
model_validate(clf,m,y)

Result of k-fold cross validation on  MultinomialNB
0.5860285714285715


In [106]:
print(new_x.shape)

NameError: name 'new_x' is not defined

In [73]:
# print(type(x))
# print(x)
matrix = np.asmatrix(x)
print(matrix)

[[<70000x59109 sparse matrix of type '<class 'numpy.float64'>'
	with 1169985 stored elements in Compressed Sparse Row format>]]


In [ ]:
x,y = preprocess()
print(x.shape)
y2 = preprocess_testing()
print(y2.shape)

In [175]:
print(vectorizer.get_feature_names())

  (0, 22632)	1
  (0, 6394)	3
  (0, 25040)	1
  (0, 49543)	5
  (0, 10205)	1
  (0, 1908)	1
  (0, 40958)	1
  (0, 36519)	1
  (0, 25734)	1
  (0, 49523)	1
  (0, 29720)	1
  (0, 18126)	3
  (0, 47055)	1
  (0, 20038)	1
  (0, 53925)	3
  (0, 19121)	1
  (0, 19628)	1
  (0, 49755)	1
  (0, 14772)	1
  (0, 18629)	1
  (0, 34423)	1
  (0, 50873)	1
  (0, 4620)	1
  (0, 36054)	1
  (0, 34386)	2
  (0, 55815)	1
  (0, 6632)	1
  (0, 48625)	1
  (0, 12488)	1
  (0, 49354)	1
  (0, 9358)	1
  (0, 32228)	1
  (0, 31961)	1
  (0, 41375)	1
  (0, 7811)	1
  (0, 50212)	1
  (0, 13961)	1
  (0, 28870)	1
{'movies', 'baseball', 'nba', 'canada', 'hockey', 'Overwatch', 'GlobalOffensive', 'wow', 'gameofthrones', 'worldnews', 'Music', 'funny', 'nfl', 'europe', 'soccer', 'trees', 'AskReddit', 'anime', 'conspiracy', 'leagueoflegends'}


In [152]:
print(vectorizer.get_feature_names())

['aa', 'aaa', 'aaaa', 'aaaaa', 'aaaaaa', 'aaaaaaaaaaaaand', 'aaaaaaaaahq', 'aaaaaaaabeq', 'aaaaaaaacxi', 'aaaaaaaaezo', 'aaaaaaaafii', 'aaaaaaaamza', 'aaaaaaaannd', 'aaaaaaaaz', 'aaaaaaabheo', 'aaaaaand', 'aaaaand', 'aaaages', 'aaaah', 'aaaand', 'aaaannnd', 'aaah', 'aaahahaha', 'aaand', 'aaannnd', 'aaawhitney', 'aabb', 'aac', 'aacnjournals', 'aaf', 'aafc', 'aah', 'aahhh', 'aahhhh', 'aaliyah', 'aam', 'aan', 'aang', 'aangechouwen', 'aardman', 'aaron', 'aarp', 'aarya', 'aasaults', 'aat', 'aatrox', 'aau', 'aav', 'aawe', 'ab', 'aba', 'aback', 'abadi', 'abam', 'abandon', 'abandoned', 'abandoning', 'abandonment', 'abandonned', 'abandonware', 'abaya', 'abb', 'abbas', 'abbey', 'abbreviated', 'abbreviation', 'abby', 'abc', 'abck', 'abd', 'abdelhak', 'abdelkader', 'abdicate', 'abdomen', 'abdominal', 'abducted', 'abducting', 'abduction', 'abductive', 'abdul', 'abdullah', 'abe', 'abeast', 'abed', 'abel', 'abell', 'abendblatt', 'aberation', 'aberdeen', 'aberg', 'aberration', 'abetting', 'abeyta', 'a

In [11]:
vectorizer = CountVectorizer()

corpus = [ 'This is a sentence',
           'Another sentence is here',
           'Wait for another sentence',
           'The sentence is coming',
           'The sentence has come'
         ]

x = vectorizer.fit_transform(corpus)
print(pd.DataFrame(x.A, columns=vectorizer.get_feature_names()).to_string())

   another  come  coming  for  has  here  is  sentence  the  this  wait
0        0     0       0    0    0     0   1         1    0     1     0
1        1     0       0    0    0     1   1         1    0     0     0
2        1     0       0    1    0     0   0         1    0     0     1
3        0     0       1    0    0     0   1         1    1     0     0
4        0     1       0    0    1     0   0         1    1     0     0


In [13]:
print(x.A)

[[0 0 0 0 0 0 1 1 0 1 0]
 [1 0 0 0 0 1 1 1 0 0 0]
 [1 0 0 1 0 0 0 1 0 0 1]
 [0 0 1 0 0 0 1 1 1 0 0]
 [0 1 0 0 1 0 0 1 1 0 0]]


In [19]:
from spellchecker import SpellChecker
spell = SpellChecker()
x = spell.correction("admires")
print(x)

admires


In [53]:
PorterStemmer().stem("abandonware")
#PorterStemmer().stem("administration")
# lemma = nltk.wordnet.WordNetLemmatizer()
# lemma.lemmatize("administr")

# x = spell.correction("administr")
# lemma.lemmatize("administer")

'abandonwar'

In [ ]:
#######################Stats memo##########################
No. of tokens: training set / test set

No operation: 62853 / 41462
    
spelling-correction: 
    
remove stopwords: 62721 / 41331
remove non-English: 20713 / 16111
remove non-Englsih/remove stopwords: 20587 / 15986
    
lemma/remove non-English: 21125 / 16518
stem/remove non-English: 10462 / 8352

    
lemma/remove non-English/remove stopwords: 21002 / 16396
stem/remove non-English/remove stopwords: 10359 / 8250

lemma/stem/remove non-English/remove stopwords: 10323 / 8236


    
